# Hyper parameter search for CQL

In [15]:
!pip install d3rlpy

In [16]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [17]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [18]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [19]:
dataset, states, actions, rewards = get_dataset([i+200 for  i in range(100)], path="../collected_data/rl_purestochastic.txt")

start
[ 0.00000000e+00  7.95731469e+08  1.43210892e-01 -3.25999953e-02
 -1.38000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.28049971e-01  6.00000000e-01  4.67532035e-01]
Read chunk # 201 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.87189108e-01  2.46000047e-02
 -8.00013420e-04  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -5.61927906e-02  2.08952959e-01]
Read chunk # 202 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.53789108e-01  1.32000047e-02
  8.79998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -9.71586383e-02 -6.00000000e-01 -5.33093061e-02]
Read chunk # 203 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.39489108e-01 -4.75999953e-02
 -9.30001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01  1.41298638e-01  5.43892365e-01]
Read chunk # 204 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.48410892e-01  5.24000047e-02
  2.50999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.

[ 0.00000000e+00  7.95731469e+08  3.96710892e-01 -1.01999953e-02
 -1.04000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -6.00000000e-01 -4.37719266e-01]
Read chunk # 250 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.07710892e-01  3.78000047e-02
 -2.22000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -7.62082511e-02  1.61745700e-01]
Read chunk # 251 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  8.62108923e-02 -1.29999953e-02
 -1.66000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -1.01419569e-01  2.01047612e-01  6.00000000e-01]
Read chunk # 252 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  6.16108923e-02 -5.77999953e-02
  2.50999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  1.10771801e-01  4.84326755e-01  6.00000000e-01]
Read chunk # 253 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  7.75108923e-02 -4.85999953e-02
  2.30999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.000000

In [20]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -269.3442,
 'std': 168.58556,
 'min': -635.52454,
 'max': 0.0,
 'histogram': (array([ 5,  3,  3,  3,  4,  2,  4,  1,  0,  2,  9,  7, 10,  7,  8,  7, 13,
         10,  1,  1]),
  array([-635.52454 , -603.7483  , -571.9721  , -540.19586 , -508.41962 ,
         -476.6434  , -444.8672  , -413.09094 , -381.31473 , -349.53848 ,
         -317.76227 , -285.98605 , -254.20981 , -222.4336  , -190.65736 ,
         -158.88113 , -127.104904,  -95.32868 ,  -63.552452,  -31.776226,
            0.      ], dtype=float32))}

In [21]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [22]:
from d3rlpy.algos import CQL
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [ ]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = CQL(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
                actor_encoder_factory = actor_encoder,
                critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                temp_learning_rate=temp_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+1000 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_cql.pkl", "wb") as f:
            print("most optimal hyper params for cql at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_cql.pt")
        model.save_policy("policy_hyperparams_cql.pt")


search iteration:  0
using hyper params:  [0.0031407135725740544, 0.0013820489635677539, 7.31673811873202e-05, 1]
2022-04-21 21:52.43 [debug    ] RoundIterator is selected.
2022-04-21 21:52.43 [info     ] Directory is created at d3rlpy_logs/CQL_20220421215243
2022-04-21 21:52.43 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-21 21:52.43 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-21 21:52.43 [warning  ] Skip building models since they're already built.
2022-04-21 21:52.43 [info     ] Parameters are saved to d3rlpy_logs/CQL_20220421215243/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'vector', 'params': {'hidden_units': [12, 24, 36, 24, 12], 'activation': 'relu', 'use_batch_norm': True, 'dropout_rate': 0.2, 'use_dense': False}}, 'actor_learning_rate': 0.0031407135725740544, 'actor_optim_factory': {'optim_cls': 'Adam', 'betas': (

Epoch 1/50:   0%|          | 0/346 [00:00<?, ?it/s]

2022-04-21 21:53.00 [info     ] CQL_20220421215243: epoch=1 step=346 epoch=1 metrics={'time_sample_batch': 0.00025672995286180793, 'time_algorithm_update': 0.048310447290453605, 'temp_loss': 4.874697296605634, 'temp': 0.9868872661811079, 'alpha_loss': -17.648908477298097, 'alpha': 1.0177169304362612, 'critic_loss': 28.417487921742346, 'actor_loss': -1.8406218001780483, 'time_step': 0.048632645882623046, 'td_error': 1.224320662493224, 'init_value': 0.07656802982091904, 'ave_value': 0.1957315176418038} step=346
2022-04-21 21:53.00 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220421215243/model_346.pt


Epoch 2/50:   0%|          | 0/346 [00:00<?, ?it/s]

2022-04-21 21:53.18 [info     ] CQL_20220421215243: epoch=2 step=692 epoch=2 metrics={'time_sample_batch': 0.0002572419326429422, 'time_algorithm_update': 0.04820082504625265, 'temp_loss': 4.856820766636402, 'temp': 0.9619505985968375, 'alpha_loss': -18.338288880497046, 'alpha': 1.0542209958065452, 'critic_loss': 29.698356832382995, 'actor_loss': -1.7210954730910373, 'time_step': 0.04852366378541627, 'td_error': 1.212277606704511, 'init_value': -0.12082002311944962, 'ave_value': 0.10047348111730127} step=692
2022-04-21 21:53.18 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220421215243/model_692.pt


...

Epoch 25/50:   0%|          | 0/346 [00:00<?, ?it/s]

2022-04-22 08:54.38 [info     ] CQL_20220422084918: epoch=25 step=8650 epoch=25 metrics={'time_sample_batch': 0.0003363872539101308, 'time_algorithm_update': 0.035433769915145255, 'temp_loss': 3.8491937659379376, 'temp': 0.7622843179744103, 'alpha_loss': -43.586108246290614, 'alpha': 2.5066244361028507, 'critic_loss': 3691.11342166614, 'actor_loss': 11.137667937085808, 'time_step': 0.03585418800398105, 'td_error': 1.4818454667115988, 'init_value': -12.757338523864746, 'ave_value': -12.76156118084549} step=8650
2022-04-22 08:54.38 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220422084918/model_8650.pt


Epoch 26/50:   0%|          | 0/346 [00:00<?, ?it/s]

2022-04-22 08:54.50 [info     ] CQL_20220422084918: epoch=26 step=8996 epoch=26 metrics={'time_sample_batch': 0.00034888493532390263, 'time_algorithm_update': 0.03487764893239633, 'temp_loss': 3.807430429265678, 'temp': 0.7539667252860317, 'alpha_loss': -45.28020405631534, 'alpha': 2.6041824142367855, 'critic_loss': 3552.2794549313585, 'actor_loss': 11.696581545592732, 'time_step': 0.03530953936494155, 'td_error': 1.5035161830144845, 'init_value': -13.511636734008789, 'ave_value': -13.508767803476116} step=8996
2022-04-22 08:54.50 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220422084918/model_8996.pt


Epoch 27/50:   0%|          | 0/346 [00:00<?, ?it/s]

## Reading hyper params from file

In [ ]:
with open("hyperparams_cql.pkl", "rb") as f:
    data = pkl.load(f)

print(data)